In [1]:
import wandb
import sys
import matplotlib.pyplot as plt
import scprep
import pandas as pd
sys.path.append('../../src/')
from train import load_data
# from diffusion import DiffusionModel
# from evaluate import get_results
from omegaconf import OmegaConf
# from main import load_data, make_model
import numpy as np
import os
import glob
import matplotlib.animation as animation
from matplotlib.animation import PillowWriter
import torch
from model2 import Autoencoder, Preprocessor
import magic
import torch
import pathlib
from procrustes import Procrustes
from plotly3d.plot import scatter

wandb.login()
api = wandb.Api()

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: xingzhis. Use `wandb login --relogin` to force relogin


In [2]:
entity = "xingzhis"
project = "dmae"
sweep_id = 'cae9f2b3'
sweep = api.sweep(f"{entity}/{project}/{sweep_id}")
# Initialize an empty list to store run data
runs_data = []

# Iterate through each run in the sweep
for run in sweep.runs:
    # Extract metrics and configs
    metrics = run.summary._json_dict
    configs = run.config
    
    # Combine metrics and configs, and add run ID
    combined_data = {**metrics, **configs, "run_id": run.id}
    
    # Append the combined data to the list
    runs_data.append(combined_data)

# Create a DataFrame from the runs data
df = pd.DataFrame(runs_data)

In [3]:
len(np.unique([run.id for run in sweep.runs]))

56

In [4]:
len(df['run_id'].unique())

56

In [5]:
df.shape

(60, 86)

In [6]:
df['data.name'].unique()

array(['eb', 'hemisphere_hi_dim2', 'hemisphere', 'tree',
       'swiss_roll_sklearn'], dtype=object)

In [7]:
df['cfg/data/root'].unique()

array(['../data/negative_sampling_toy1/False/'], dtype=object)

In [8]:
df.columns

Index(['_timestamp', 'train/loss_step', 'train/dist_loss_step',
       'train/reconstr_loss_step', 'validation/dist_loss',
       'train/cycle_loss_step', 'train/loss_negative_epoch',
       'train/loss_negative_step', 'validation/loss_negative', '_wandb',
       'train/loss_epoch', 'trainer/global_step', 'train/dist_loss_epoch',
       'train/cycle_loss_epoch', 'validation/reconstr_loss',
       'train/reconstr_loss_epoch', '_step', 'epoch', '_runtime',
       'validation/loss', 'validation/cycle_loss', 'data', 'loss', 'path',
       'logger', 'decoder', 'encoder', 'training', 'data.name', 'data.root',
       'dimensions', 'cfg/path/log', 'preprocessor', 'cfg/data/name',
       'cfg/data/root', 'cfg/path/root', 'training.mode', 'cfg/path/model',
       'cfg/logger/tags', 'cfg/training/lr', 'decoder.dropout',
       'encoder.dropout', 'cfg/data/filetype', 'cfg/logger/entity',
       'cfg/training/mode', 'cfg/training/seed', 'dimensions.latent',
       'loss.weights.dist', 'cfg/logger/p

In [9]:
df[(df['data.name'] == 'hemisphere') & (df['cfg/loss/weights/cycle'] == 1.) & (df['cfg/data/root'] == '../data/negative_sampling_toy1/True/') & (df['cfg/dimensions/latent'] == 2) & (df['cfg/loss/weights/dist']> 10)][['run_id']]


Empty DataFrame
Columns: [run_id]
Index: []

In [10]:
df['cfg/data/root'].value_counts()

cfg/data/root
../data/negative_sampling_toy1/False/    60
Name: count, dtype: int64

In [13]:
df[(df['data.name'] == 'hemisphere') & (df['cfg/loss/weights/cycle'] == 1.) & (df['cfg/data/root'] == '../data/negative_sampling_toy1/False/') & (df['cfg/dimensions/latent'] == 2) & (df['cfg/loss/weights/negative'] == 1.)][['run_id']]


run_id
31  f9rsgp0z

In [14]:
run_ids = df[(df['data.name'] == 'hemisphere') & (df['cfg/loss/weights/cycle'] == 1.) & (df['cfg/data/root'] == '../data/negative_sampling_toy1/False/') & (df['cfg/dimensions/latent'] == 2) & (df['cfg/loss/weights/negative'] == 10.)][['run_id']]
assert len(run_ids) == 1
run_id = run_ids.iloc[0]
run = api.run(f"{entity}/{project}/{run_ids.iloc[0].values[0]}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
model = Autoencoder.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    model.eval()
    x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
    z = model.encoder(x)
    xh = model.decoder(z)
    zhh = model.encoder(xh)
zc = z.cpu().numpy()
filename = None
savefolder = None
plot_x = True
plot_recon = True
# title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
title = ''
if savefolder is not None:
    pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
    filename = f"{savefolder}/{title}.html"
scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
scatter(zhh, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
if plot_x:
    title1 = f'[INPUT DATA] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(x, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()
if plot_recon:
    title = f'[RECON] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(xh, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/utilities/parsing.py:269: UserWarning: Attribute 'preprocessor' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['preprocessor'])`.
  rank_zero_warn(


In [18]:
run_ids = df[(df['data.name'] == 'hemisphere') & (df['cfg/loss/weights/cycle'] == 1.) & (df['cfg/data/root'] == '../data/negative_sampling_toy1/False/') & (df['cfg/dimensions/latent'] == 3) & (df['cfg/loss/weights/negative'] == 10.)][['run_id']]
assert len(run_ids) == 1
run_id = run_ids.iloc[0]
run = api.run(f"{entity}/{project}/{run_ids.iloc[0].values[0]}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
model = Autoencoder.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    model.eval()
    x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
    z = model.encoder(x)
    xh = model.decoder(z)
    zhh = model.encoder(xh)
zc = z.cpu().numpy()
filename = None
savefolder = None
plot_x = True
plot_recon = True
# title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
title = ''
if savefolder is not None:
    pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
    filename = f"{savefolder}/{title}.html"
scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
scatter(zhh, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
if plot_x:
    title1 = f'[INPUT DATA] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(x, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()
if plot_recon:
    title = f'[RECON] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(xh, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/pytorch_lightning/utilities/parsing.py:269: UserWarning:

Attribute 'preprocessor' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['preprocessor'])`.



In [ ]:
run_ids = df[(df['data.name'] == 'hemisphere_hi_dim2') & (df['cfg/loss/weights/cycle'] == 1.) & (df['cfg/data/root'] == '../data/negative_sampling_toy/False/') & (df['cfg/dimensions/latent'] == 3) & (df['cfg/loss/weights/negative'] == 1.)][['run_id']]
assert len(run_ids) == 1
run_id = run_ids.iloc[0]
run = api.run(f"{entity}/{project}/{run_ids.iloc[0].values[0]}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
model = Autoencoder.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    model.eval()
    x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
    z = model.encoder(x)
    xh = model.decoder(z)
    zhh = model.encoder(xh)
zc = z.cpu().numpy()
filename = None
savefolder = None
plot_x = True
plot_recon = True
# title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
title = ''
if savefolder is not None:
    pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
    filename = f"{savefolder}/{title}.html"
scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
scatter(zhh, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
if plot_x:
    title1 = f'[INPUT DATA] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(x, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()
if plot_recon:
    title = f'[RECON] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(xh, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()


: 

In [ ]:
run_ids = df[(df['data.name'] == 'eb') & (df['cfg/loss/weights/cycle'] == 1.) & (df['cfg/data/root'] == '../data/negative_sampling_toy/False/') & (df['cfg/dimensions/latent'] == 3) & (df['cfg/loss/weights/negative'] == 1.)][['run_id']]
assert len(run_ids) == 1
run_id = run_ids.iloc[0]
run = api.run(f"{entity}/{project}/{run_ids.iloc[0].values[0]}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
model = Autoencoder.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    model.eval()
    x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
    z = model.encoder(x)
    xh = model.decoder(z)
    zhh = model.encoder(xh)
zc = z.cpu().numpy()
filename = None
savefolder = None
plot_x = True
plot_recon = True
# title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
title = ''
if savefolder is not None:
    pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
    filename = f"{savefolder}/{title}.html"
scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
scatter(zhh, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
if plot_x:
    title1 = f'[INPUT DATA] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(x, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()
if plot_recon:
    title = f'[RECON] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(xh, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()


: 

In [ ]:
run_ids = df[(df['data.name'] == 'swiss_roll_sklearn') & (df['cfg/loss/weights/cycle'] == 1.) & (df['cfg/data/root'] == '../data/negative_sampling_toy/False/') & (df['cfg/dimensions/latent'] == 2) & (df['cfg/loss/weights/negative'] == 10.)][['run_id']]
assert len(run_ids) == 1
run_id = run_ids.iloc[0]
run = api.run(f"{entity}/{project}/{run_ids.iloc[0].values[0]}")
folder_path = '../../src/wandb/'
cfg = OmegaConf.create(run.config)
folder_list = glob.glob(f"{folder_path}*{run.id}*")
ckpt_files = glob.glob(f"{folder_list[0]}/files/*.ckpt")
ckpt_path = ckpt_files[0]
cfg.data.root = '../' + cfg.data.root
model = Autoencoder.load_from_checkpoint(ckpt_path)
data = np.load(f"{cfg.data.root}/{cfg.data.name}{cfg.data.filetype}", allow_pickle=True)
with torch.no_grad():
    model.eval()
    x = torch.tensor(data['data'], dtype=torch.float32, device=model.device)
    z = model.encoder(x)
    xh = model.decoder(z)
    zhh = model.encoder(xh)
zc = z.cpu().numpy()
filename = None
savefolder = None
plot_x = True
plot_recon = True
# title = f'{data_name} {noise_type} {noise_level} {dist_mask}'
title = ''
if savefolder is not None:
    pathlib.Path(savefolder).mkdir(parents=True, exist_ok=True)
    filename = f"{savefolder}/{title}.html"
scatter(zc, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
scatter(zhh, data['mask_x'], s=2, alpha=0.2, title=title, filename=filename).show()
if plot_x:
    title1 = f'[INPUT DATA] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(x, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()
if plot_recon:
    title = f'[RECON] {title}'
    if savefolder is not None:
        filename = f"{savefolder}/{title1}.html"
    scatter(xh, data['mask_x'], s=2, alpha=0.2, title=title1, filename=filename).show()


: 

: 